### 2022年度計算機演習A・B

# 第14回：フラクタル1

**フラクタル（fractal）**とは、「自己相似性」（全体と部分が相似となる性質）を持つような図形のことです。

今回と次回の授業では、プログラミングによっていくつかのフラクタルの描画を行います。

※フラクタルは通常、ある特定の操作を無限回繰り返すことで得られますが、プログラミングでそれは実現できないため、以下では有限回繰り返した結果を描画することにします。

## 1. コッホ曲線

**コッホ曲線（Koch curve）**は特に有名なフラクタルであり、次のようにして得られます。

<div align="center"><img src="https://upload.wikimedia.org/wikipedia/commons/6/6f/How_to_make_Koch_curve.svg" width="600"></div>

- ステップ1：与えられた線分を3等分し、中央の線分を1辺とする正三角形を外側に描いて内側の辺を消す（左上→右上）。

- ステップ2：得られた4本の線分に対して同様の操作を行う（右上→左下）。

- ステップ3：得られた16本の線分に対して同様の操作を行う（左下→右下）。

- …

以下では、3つの関数を定義することによって、コッホ曲線を描画するプログラムを作成します。

まず、複数の点からなる行列`nodes`に対して、それらを順に結んだ線分を描画する関数`draw_segments(nodes)`を定義します。

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

def draw_segments(nodes):
    #nodes[0,:]はx座標の配列、nodes[1,:]はy座標の配列
    plt.plot(nodes[0,:],nodes[1,:],"b")
    plt.grid()
    plt.gca().set_aspect("equal")
    plt.show()

nodes = np.array([[0,0],[1,0]]).T  #点ごとに入力してから転置すると簡単
draw_segments(nodes)  #関数を呼び出して線分を描画する

次に、2つの点からなる行列`two_nodes`に対して、その線分に必要な操作を行った結果の点を追加した行列を返す関数`add_nodes(two_nodes)`を定義します。

ここで、元の行列を

$$
\begin{pmatrix}
p_0 & p_1
\end{pmatrix}
$$

とすれば、関数が返すべき行列は下図における

$$
\begin{pmatrix}
p_0 & p_2 & p_4 & p_3 & p_1
\end{pmatrix}
$$

です。

<div align="center"><img src="https://www.ces-alpha.org/course/file_serve/5666228794294272/figure14-1.png" width="450"></div>

$p_2$ と $p_3$ は線分 $p_0p_1$ をそれぞれ $1:2$ と $2:1$ に内分する点であるため、

$$
p_2=\frac{2}{3}p_0+\frac{1}{3}p_1,\quad p_3=\frac{1}{3}p_0+\frac{2}{3}p_1
$$

となり、$p_4$ は $p_2$ を中心に $p_3$ を反時計回りに60度回転させた点であるため、

$$
p_4=p_2+
\begin{pmatrix}
\cos\theta & -\sin\theta\\
\sin\theta & \cos\theta
\end{pmatrix}
(p_3-p_2),\quad \theta=\frac{60\pi}{180}
$$

が成り立ちます。

In [ ]:
def add_nodes(two_nodes):
    p0 = two_nodes[:,0]
    p1 = two_nodes[:,1]
    p2 = 2/3*p0+1/3*p1  #内分
    p3 = 1/3*p0+2/3*p1
    theta = 60/180*np.pi
    A = np.array([[np.cos(theta),-np.sin(theta)],[np.sin(theta),np.cos(theta)]])  #回転行列
    p4 = p2+A@(p3-p2)  #p0～p3は一次元配列だが、A@の計算は問題なくできる
    return np.array([p0,p2,p4,p3,p1]).T

two_nodes = np.array([[0,0],[1,0]]).T
nodes = add_nodes(two_nodes)
draw_segments(nodes)

さらに、複数の点からなる行列`nodes`に対して、各線分に`add_nodes`を行った結果の行列を返す関数`update_nodes(nodes)`を定義します。

In [ ]:
def update_nodes(nodes):
    new_nodes = [nodes[:,0]]  #最初の点のみからなるリスト
    for i in range(nodes.shape[1]-1):  #0からnodesの列数-2まで変化させる
        two_nodes = nodes[:,[i,i+1]]  #nodesの点を2つずつ使用する
        tmp_nodes = add_nodes(two_nodes)  #add_nodesを呼び出して行列を返す
        for j in range(1,5):
            new_nodes.append(tmp_nodes[:,j])  #リストにtmp_nodesの最初以外の点を追加する
    return np.array(new_nodes).T
    #隣り合う線分は片方の端点を共有しているため、点を重複させないために上のような処理になる

nodes = np.array([[0,0],[1,0]]).T
nodes = update_nodes(nodes)  #1回目の繰り返し
nodes = update_nodes(nodes)  #2回目の繰り返し
draw_segments(nodes)

コードをまとめると、次のようになります。

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

def draw_segments(nodes):
    plt.plot(nodes[0,:],nodes[1,:],"b")
    plt.grid()
    plt.gca().set_aspect("equal")
    plt.show()

def add_nodes(two_nodes):
    p0 = two_nodes[:,0]
    p1 = two_nodes[:,1]
    p2 = 2/3*p0+1/3*p1
    p3 = 1/3*p0+2/3*p1
    theta = 60/180*np.pi
    A = np.array([[np.cos(theta),-np.sin(theta)],[np.sin(theta),np.cos(theta)]])
    p4 = p2+A@(p3-p2)
    return np.array([p0,p2,p4,p3,p1]).T

def update_nodes(nodes):
    new_nodes = [nodes[:,0]]
    for i in range(nodes.shape[1]-1):
        two_nodes = nodes[:,[i,i+1]]
        tmp_nodes = add_nodes(two_nodes)
        for j in range(1,5):
            new_nodes.append(tmp_nodes[:,j])
    return np.array(new_nodes).T

nodes = np.array([[0,0],[1,0]]).T
n = 3  #繰り返し回数（値を変化させてみるとよい）
for k in range(n):
    nodes = update_nodes(nodes)
draw_segments(nodes)

### 演習1

正三角形から得られるコッホ曲線を**コッホ雪片（Koch snowflake）**と呼びます。

上記のコードを利用して、コッホ雪片を描画してください。ただし、繰り返し回数は5回とします。

In [ ]:
#演習1のコード

#正三角形の頂点の座標は各自で決める
#点が時計回りになるようにnodesを定める必要がある

### 演習2

コッホ曲線を得るための操作における分割点の位置や角度を変えることによって、自分なりの新しいフラクタルを作成して描画してください。

In [ ]:
#演習2のコード

## 2. ミンコフスキーのソーセージ

**ミンコフスキーのソーセージ（Minkowski sausage）**は、下図のように線分（黒）から3本の線分（赤）を作成する操作を繰り返すことによって得られるフラクタルです。図中の数値は、線分の比を表しています。

※ミンコフスキーのソーセージにはいくつかのバリエーションがあり、ここではそのうちの一つを紹介します。

<div align="center"><img src="https://www.ces-alpha.org/course/file_serve/5724059664908288/figure14-2.png" width="500"></div>

元の行列

$$
\begin{pmatrix}
p_0 & p_1
\end{pmatrix}
$$

から新たな行列

$$
\begin{pmatrix}
p_0 & p_2 & p_3 & p_1
\end{pmatrix}
$$

を求める方法は次の通りです。

- 線分 $p_0p_1$ 上で $|p_0q|=\frac{1}{\sqrt{5}}|p_0p_1|$ を満たす $q$ を求めます。

- $p_0$ を中心に $q$ を時計回りに $\theta=\sin^{-1}\left(\frac{1}{\sqrt{5}}\right)$ 回転させた点が $p_2$ です。

- 線分 $p_0p_1$ 上で $|p_1r|=\frac{1}{\sqrt{5}}|p_0p_1|$ を満たす $r$ を求めます。

- $p_1$ を中心に $r$ を時計回りに $\theta=\sin^{-1}\left(\frac{1}{\sqrt{5}}\right)$ 回転させた点が $p_3$ です。

### 演習3（オプション）

正方形から得られるミンコフスキーのソーセージを描画してください。ただし、繰り返し回数は5回とします。

In [ ]:
#演習3のコード

#sinの逆関数は「np.arcsin()」を使えばよい

## 第14回レポート課題

演習1～演習3に取り組んでください。